In [2]:
import os
import dask
import json
from os.path import join, dirname, expanduser, splitext, basename
import numpy as np
from glob import glob
import matplotlib.pyplot as plt
import geopandas as gpd
import pandas as pd
import leafmap.leafmap as leafmap
from dotenv import load_dotenv
import xarray as xr
import rioxarray as rxr
from PIL import Image
from shapely.geometry import mapping, Polygon
from tqdm.notebook import tqdm
from joblib import Parallel, delayed

# import delayed from dask
import dask

load_dotenv()

True

In [3]:
state="rajshahi"
save_region="rajshahi"

base_path="/home/rishabh.mondal/Brick-Kilns-project/ijcai_2025_kilns"
mosaic_id="global_quarterly_2024q1_mosaic"
image_meta_data=f"{base_path}/raw_data/metadata/{state}/{mosaic_id}/metadata.geojson"
imagery_dir = f"{base_path}/raw_data/imagery/{mosaic_id}"
state_label_path=f"/home/rishabh.mondal/Brick-Kilns-project/ijcai_2025_kilns/after_hand_validation_data/bangladesh_v1/{state}.geojson"

stete_shape_path=f"{base_path}/regions/shapes/{state}.geojson"
save_dir=f"../data/processed_data/{state}/"
os.makedirs(save_dir, exist_ok=True)

print(f"state: {state}")
print(f"base_path: {base_path}")
print(f"mosaic_id: {mosaic_id}")
print(f"image_meta_data: {image_meta_data}")
print(f"imagery_dir: {imagery_dir}")
print(f"state_label_path: {state_label_path}")
print(f"stete_shape_path: {stete_shape_path}")
print(f"save_dir: {save_dir}")
# with open("/home/patel_zeel/kiln_compass_24/other_data/wayback_imagery.json") as f:
#     wayback_imagery = json.load(f)
    
# wayback_url = wayback_imagery['2024-02-08']

state: rajshahi
base_path: /home/rishabh.mondal/Brick-Kilns-project/ijcai_2025_kilns
mosaic_id: global_quarterly_2024q1_mosaic
image_meta_data: /home/rishabh.mondal/Brick-Kilns-project/ijcai_2025_kilns/raw_data/metadata/rajshahi/global_quarterly_2024q1_mosaic/metadata.geojson
imagery_dir: /home/rishabh.mondal/Brick-Kilns-project/ijcai_2025_kilns/raw_data/imagery/global_quarterly_2024q1_mosaic
state_label_path: /home/rishabh.mondal/Brick-Kilns-project/ijcai_2025_kilns/after_hand_validation_data/bangladesh_v1/rajshahi.geojson
stete_shape_path: /home/rishabh.mondal/Brick-Kilns-project/ijcai_2025_kilns/regions/shapes/rajshahi.geojson
save_dir: ../data/processed_data/rajshahi/


In [4]:
gdf_labels = gpd.read_file(state_label_path).drop("style", errors="ignore", axis=1)
# print(gdf_labels.head())
color_mapping = {"CFCBK": "red", "FCBK": "orange", "Zigzag": "green"}
gdf_labels["style"] = gdf_labels["class_name"].apply(lambda x: {"color": color_mapping[x]})
# print(gdf_labels.head())
gdf_images = gpd.read_file(image_meta_data)
print(gdf_images.head())
print(len(gdf_labels), len(gdf_images))
gdf_image_paths = [join(f"{base_path}/raw_data/imagery/global_quarterly_2024q1_mosaic", f"{Id}.tif") for Id in gdf_images["id"]]
print(len(gdf_image_paths))
# print(gdf_image_paths[:5])



                                               _self  \
0  https://api.planet.com/basemaps/v1/mosaics/a37...   
1  https://api.planet.com/basemaps/v1/mosaics/a37...   
2  https://api.planet.com/basemaps/v1/mosaics/a37...   
3  https://api.planet.com/basemaps/v1/mosaics/a37...   
4  https://api.planet.com/basemaps/v1/mosaics/a37...   

                                            download  \
0  https://link.planet.com/basemaps/v1/mosaics/a3...   
1  https://link.planet.com/basemaps/v1/mosaics/a3...   
2  https://link.planet.com/basemaps/v1/mosaics/a3...   
3  https://link.planet.com/basemaps/v1/mosaics/a3...   
4  https://link.planet.com/basemaps/v1/mosaics/a3...   

                                               items  \
0  https://api.planet.com/basemaps/v1/mosaics/a37...   
1  https://api.planet.com/basemaps/v1/mosaics/a37...   
2  https://api.planet.com/basemaps/v1/mosaics/a37...   
3  https://api.planet.com/basemaps/v1/mosaics/a37...   
4  https://api.planet.com/basemaps/v1/mosaics/

# images processing

In [5]:
m=leafmap.Map()
m.add_basemap("HYBRID")
m.add_geojson(image_meta_data,zoom_to_layer=True)
m

Map(center=[20, 0], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title', 'zoom_out_text…

In [6]:
size_in_gb = sum([os.path.getsize(fp)/1024/1024/1024 for fp in gdf_image_paths])
print(f"Total size of images: {size_in_gb:.2f} GB")

Total size of images: 3.63 GB


In [7]:
print(len(gdf_image_paths))
x = np.unique(np.concatenate([xr.open_dataset(path).x.values for path in gdf_image_paths]))
x.sort()
xdiff_index = pd.Series(x).diff().value_counts().index
print(xdiff_index)
print(x)
print(len(x),len(x)/4096)
print(len(gdf_image_paths))
y = np.unique(np.concatenate([xr.open_dataset(path).y.values for path in gdf_image_paths]))
y.sort()
diff_index = pd.Series(y).diff().value_counts().index
print(diff_index)
print(len(y), len(y)/4096)

78
Index([ 4.777314268052578,  4.777314266189933, 4.7773139998316765,
        4.777315000072122,  4.777314001694322],
      dtype='float64')
[9783942.007807   9783946.78512127 9783951.56243553 ... 9999174.34748547
 9999179.12479973 9999183.902114  ]
45056 11.0
78
Index([ 4.777314267121255,  4.777314267586917, 4.7773139998316765,
        4.777314000297338,  4.777315000072122],
      dtype='float64')
40960 10.0


In [8]:
# import xarray as xr

# # Load one file to inspect its `y` values
# ds = xr.open_dataset(gdf_image_paths[0])  # Replace with an actual path if needed
# print(ds.y.values)
# ds = xr.open_dataset(gdf_image_paths[0])  # Replace with a single file
# if not (ds.y.values[0] < ds.y.values[-1]):  # Check if `y` is not increasing
#     ds = ds.sortby('y')  # Sort by the `y` dimension
# print(ds.y.values)
# sorted_datasets = []
# for path in gdf_image_paths:
#     ds = xr.open_dataset(path)
#     if not (ds.y.values[0] < ds.y.values[-1]):  # Check if `y` is not increasing
#         ds = ds.sortby('y')
#     sorted_datasets.append(ds)



In [9]:
# for path in gdf_image_paths:
#     ds = xr.open_dataset(path)
#     if not (ds.y.values[0] < ds.y.values[-1]):  # Check and sort
#         ds = ds.sortby('y')
#     ds.to_netcdf(path)  # Overwrite the file with sorted dimensions


In [10]:
# combined_ds = xr.combine_by_coords(sorted_datasets)
# print(combined_ds)


In [11]:
ds=xr.open_mfdataset(gdf_image_paths)
print(ds)
assert len(ds.x.values) % 4096 == 0
assert len(ds.y.values) % 4096 == 0

<xarray.Dataset> Size: 30GB
Dimensions:      (band: 4, y: 40960, x: 45056)
Coordinates:
  * band         (band) int64 32B 1 2 3 4
  * x            (x) float64 360kB 9.784e+06 9.784e+06 ... 9.999e+06 9.999e+06
  * y            (y) float64 328kB 2.916e+06 2.916e+06 ... 2.72e+06 2.72e+06
    spatial_ref  int64 8B 0
Data variables:
    band_data    (band, y, x) float32 30GB dask.array<chunksize=(1, 512, 512), meta=np.ndarray>


In [12]:
image_size=640
overlap=64
gap_between_centers=image_size-overlap
x_centers=[image_size//2]
x_centers.extend(list(range(x_centers[0]+gap_between_centers, len(ds.x), gap_between_centers)))
x_centers=x_centers[:-1]
y_centers=[image_size//2]
y_centers.extend(list(range(y_centers[0]+gap_between_centers, len(ds.y), gap_between_centers)))
y_centers=y_centers[:-1]
print(len(x_centers), len(y_centers))

77 70


In [13]:
x_values=ds.x.values
y_values=ds.y.values

def get_geometry(x_idx,y_idx):
    start_x=x_values[x_idx-image_size//2] #left boundary
    start_y=y_values[y_idx-image_size//2] #buttom boundary
    end_x=x_values[x_idx+image_size//2] #right boundary
    end_y=y_values[y_idx+image_size//2] #top boundary
    return Polygon([(start_x,start_y),(end_x,start_y),(end_x,end_y),(start_x,end_y)])

print(get_geometry(x_centers[0],y_centers[0]))

X,Y=np.meshgrid(x_centers,y_centers)
geometries=[get_geometry(x,y) for x,y in tqdm(zip(X.ravel(),Y.ravel()))]
x_indices=[x for x in X.ravel()]
y_indices=[y for y in Y.ravel()]
print(len(geometries),len(x_indices),len(y_indices))


POLYGON ((9783942.007807 2915611.617854, 9786999.48893798 2915611.617854, 9786999.48893798 2912554.136723021, 9783942.007807 2912554.136723021, 9783942.007807 2915611.617854))


0it [00:00, ?it/s]

5390 5390 5390


In [14]:
x_indices
y_indices

[320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 320,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 896,
 1472,
 1472,
 1472,
 1472,
 1472,
 1472,
 1472,
 1472,
 1472,
 1472,
 1472,

In [15]:
potential_image_gdf=gpd.GeoDataFrame(geometry=geometries)
print(len(potential_image_gdf))
potential_image_gdf["x_idx"]=x_indices
potential_image_gdf["y_idx"]=y_indices
potential_image_gdf.reset_index(inplace=True,drop=True)
print(ds.rio.crs)   
potential_image_gdf.crs=ds.rio.crs
print("number of potential images: ",len(potential_image_gdf))
potential_image_gdf.head(2)


5390
EPSG:3857
number of potential images:  5390


geometry  x_idx  y_idx
0  POLYGON ((9783942.008 2915611.618, 9786999.489...    320    320
1  POLYGON ((9786693.741 2915611.618, 9789751.222...    896    320

In [16]:
shape_gdf=gpd.read_file(stete_shape_path)
print(shape_gdf.crs)
shape_gdf=shape_gdf.to_crs("EPSG:3857")
assert potential_image_gdf.crs == shape_gdf.crs
print(shape_gdf.crs)
images_within_shape = gpd.sjoin(shape_gdf, potential_image_gdf, predicate="contains")
images_within_shape = potential_image_gdf.loc[images_within_shape.index_right]
display(images_within_shape.head(2))
len(images_within_shape)



EPSG:4326
EPSG:3857


geometry  x_idx  y_idx
4753  POLYGON ((9938039.057 2747755.904, 9941096.538...  32576  35456
4754  POLYGON ((9940790.79 2747755.904, 9943848.271 ...  33152  35456

2724

In [17]:
#save the grid of potential images within the state boundary as a kml file for visualization
# images_within_shape.to_file(f"{save_dir}/potential_images_within_state_boundary.kml",driver="KML")


In [18]:
m = leafmap.Map()
m.add_basemap("HYBRID")
m.add_gdf(shape_gdf, layer_name="Shape", style={"color": "black"})
m.add_gdf(images_within_shape, layer_name="Images within shape",zoom_to_layer=True)
m

Map(center=[20, 0], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title', 'zoom_out_text…

In [19]:
images_within_shape['x'] = images_within_shape['x_idx'].apply(lambda x: int(x_values[x]))
images_within_shape['y'] = images_within_shape['y_idx'].apply(lambda x: int(y_values[x]))
images_within_shape.head(6)

geometry  x_idx  y_idx  \
4753  POLYGON ((9938039.057 2747755.904, 9941096.538...  32576  35456   
4754  POLYGON ((9940790.79 2747755.904, 9943848.271 ...  33152  35456   
4675  POLYGON ((9935287.324 2750507.637, 9938344.805...  32000  34880   
4677  POLYGON ((9940790.79 2750507.637, 9943848.271 ...  33152  34880   
4593  POLYGON ((9921528.659 2753259.37, 9924586.14 2...  29120  34304   
4592  POLYGON ((9918776.926 2753259.37, 9921834.407 ...  28544  34304   

            x        y  
4753  9939567  2746227  
4754  9942319  2746227  
4675  9936816  2748978  
4677  9942319  2748978  
4593  9923057  2751730  
4592  9920305  2751730

In [184]:
os.makedirs(f"../data/processed_data/{save_region}", exist_ok=True)
images_within_shape.reset_index(drop=True).to_file(f"../data/processed_data/{save_region}/metadata.geojson", driver="GeoJSON")

In [185]:
samples = []
x_idx_list = []
y_idx_list = []
for x_idx, y_idx in tqdm(zip(images_within_shape["x_idx"], images_within_shape["y_idx"])):
    x = x_values[x_idx]
    y = y_values[y_idx]
    save_path = join(save_dir, "images", f"{int(x)}_{int(y)}.tif")
    if os.path.exists(save_path):
        try:
            image = Image.open(save_path)
            assert image.size == (image_size, image_size)
            continue
        except Exception as e:
            print(f"Error: {e}")
            print(f"Loading {save_path} failed. Overwriting the file.")
    sample = ds.isel(x=slice(x_idx - image_size//2, x_idx + image_size//2), y=slice(y_idx - image_size//2, y_idx + image_size//2), band=slice(0, 3))
    samples.append(sample)
    x_idx_list.append(x_idx)
    y_idx_list.append(y_idx)

0it [00:00, ?it/s]

In [186]:
print(len(samples), len(x_idx_list), len(y_idx_list))

0 0 0


In [94]:
def save_sample(sample, x_idx, y_idx):
    x = x_values[x_idx]
    y = y_values[y_idx]
    save_path = join(save_dir, "images", f"{int(x)}_{int(y)}.tif")
    
    sample = sample.band_data.load()
    # fill NaN values with 0
    sample = sample.fillna(0)
    # convert to uint8
    sample = sample.astype(np.uint8)
    sample.rio.to_raster(save_path)
    del sample

In [95]:
delayed_tasks = [dask.delayed(save_sample)(sample, x_idx, y_idx) for sample, x_idx, y_idx in tqdm(zip(samples, x_idx_list, y_idx_list))]
print("Number of delayed tasks:", len(delayed_tasks))

0it [00:00, ?it/s]

Number of delayed tasks: 1782


In [96]:
os.makedirs(join(save_dir, "images"), exist_ok=True)
for i in tqdm(range(0, len(delayed_tasks), 1000)):
    _ = dask.compute(*delayed_tasks[i:i+1000])

  0%|          | 0/2 [00:00<?, ?it/s]

# Labels Processing

In [20]:
## Load the state geojson
gdf_labels_webm=gdf_labels.to_crs(potential_image_gdf.crs)
gdf_labels_webm.reset_index(inplace=True, drop=True)
print(gdf_labels_webm.crs)
print("Number of labels:", len(gdf_labels_webm))

gdf_labels_webm.head(2)

PROJCS["WGS 84 / Pseudo-Mercator",GEOGCS["WGS 84",DATUM["WGS_1984",SPHEROID["WGS 84",6378137,298.257223563,AUTHORITY["EPSG","7030"]],AUTHORITY["EPSG","6326"]],PRIMEM["Greenwich",0,AUTHORITY["EPSG","8901"]],UNIT["degree",0.0174532925199433,AUTHORITY["EPSG","9122"]],AUTHORITY["EPSG","4326"]],PROJECTION["Mercator_1SP"],PARAMETER["central_meridian",0],PARAMETER["scale_factor",1],PARAMETER["false_easting",0],PARAMETER["false_northing",0],UNIT["metre",1,AUTHORITY["EPSG","9001"]],AXIS["Easting",EAST],AXIS["Northing",NORTH],EXTENSION["PROJ4","+proj=merc +a=6378137 +b=6378137 +lat_ts=0 +lon_0=0 +x_0=0 +y_0=0 +k=1 +units=m +nadgrids=@null +wktext +no_defs"],AUTHORITY["EPSG","3857"]]
Number of labels: 1018


class_name  confidence    max_lon    min_lon    max_lat    min_lat  \
0     Zigzag    0.540821  89.259472  89.258645  23.963261  23.962810   
1       FCBK    0.523977  89.254152  89.253063  23.967348  23.966788   

   center_lat  center_lon  width_of_box  height_of_box  ...         area  \
0   23.963036   89.259058     84.172590      49.951716  ...  3100.511226   
1   23.967068   89.253608    110.835623      62.024337  ...  5457.541317   

                                                  id        x        y  \
0  55838ebcab3c63571293b5de02349772a6602e3b0b894e...  9936816  2748978   
1  3b65b47ffa9c44a627cba188d87c5d2ea7af985ebd0950...  9936816  2748978   

                                          yolo_label          source  \
0  [2.       0.307323 0.519408 0.309321 0.533314 ...  hand_validated   
1  [2.       0.104058 0.356418 0.105954 0.374838 ...  hand_validated   

         task_name     type  \
0  hand_validation  polygon   
1  hand_validation  polygon   

                                            geometry                style  
0  POLYGON ((9936233.923 2748875.539, 9936327.543...   {'color': 'green'}  
1  POLYGON ((9935610.089 2749366.356, 9935715.175...  {'color': 'orange'}  

[2 rows x 22 columns]

In [21]:
images_with_label=gpd.sjoin(images_within_shape,gdf_labels_webm,predicate="contains")
images_with_label['geometry_right'] = images_with_label['index_right'].apply(lambda x: gdf_labels_webm.loc[x, 'geometry'])
print(f"Number of labels to write: {len(images_with_label)}")

print(f"Number of unique images: {len(images_with_label.drop_duplicates(subset='geometry'))}")
print(f"Number of unique labels: {len(images_with_label.drop_duplicates(subset='geometry_right'))}")

Number of labels to write: 1166
Number of unique images: 582
Number of unique labels: 1014


In [22]:
# images_within_shape
# gdf_labels_webm

In [23]:
class_mapping = {"CFCBK": 0, "FCBK": 1, "Zigzag": 2}

def get_yolo_label(x):
    min_x, min_y, max_x, max_y = x['geometry'].bounds
    coords = np.array(x['geometry_right'].__geo_interface__['coordinates'][0])
    coords = coords[:-1]
    # normalize
    coords[:, 0] = (coords[:, 0] - min_x) / (max_x - min_x)
    coords[:, 1] = 1 - (coords[:, 1] - min_y) / (max_y - min_y)
    
    coords = coords.ravel()
    assert len(coords) == 8
    
    class_id = class_mapping[x['class_name']]
    label = np.zeros(9) * np.nan
    label[0] = class_id
    label[1:] = coords
    return label



In [24]:
images_with_label['yolo_label'] = images_with_label.apply(get_yolo_label, axis=1)
images_with_label.head(2)
ready_to_save_gdf = images_with_label.groupby("geometry").agg({"yolo_label": np.vstack, "x_idx": "first", "y_idx": "first"}).reset_index()
len(ready_to_save_gdf)

582

In [25]:
ready_to_save_gdf['x'] = ready_to_save_gdf['x_idx'].apply(lambda x: str(int(x_values[x])))
ready_to_save_gdf['y'] = ready_to_save_gdf['y_idx'].apply(lambda x: str(int(y_values[x])))
len(ready_to_save_gdf)
display(ready_to_save_gdf.tail(2))

geometry  \
580  POLYGON ((9973811.586 2745004.171, 9976869.067...   
581  POLYGON ((9976563.319 2745004.171, 9979620.8 2...   

                                            yolo_label  x_idx  y_idx        x  \
580  [[2.0, 0.3066397876253859, 0.7405828838819712,...  40064  36032  9975340   
581  [[2.0, 0.3656135122348169, 0.9050675520971057,...  40640  36032  9978092   

           y  
580  2743475  
581  2743475

In [26]:
def save_label(x):
    label = x['yolo_label']
    save_path = join(save_dir, "labels", f"{x['x']}_{x['y']}.txt")
    np.savetxt(save_path, label, fmt="%d %f %f %f %f %f %f %f %f")
    
print(f"{save_dir=}")
os.makedirs(join(save_dir, "labels"), exist_ok=True)
_ = ready_to_save_gdf.apply(save_label, axis=1)

save_dir='../data/processed_data/rajshahi/'


In [238]:
save_dir=f"/home/patel_zeel/kiln_compass_24/data/{state}/"

In [26]:
label_files = glob(join(save_dir, "labels", "*.txt"))
label_file = np.random.choice(label_files)
image_file = join(save_dir, "images", basename(splitext(label_file)[0] + ".tif"))

plt.figure(figsize=(10, 10))
image = Image.open(image_file)
print(image.size)
plt.imshow(image)
plt.axis("off")

labels = np.loadtxt(label_file, ndmin=2)
for label in labels:
    label[1:] = label[1:] * image_size
    plt.plot([label[1], label[3], label[5], label[7], label[1]], [label[2], label[4], label[6], label[8], label[2]], "r-")

ValueError: 'a' cannot be empty unless no samples are taken

In [196]:
# Config
import os
import json
import geojson
import leafmap.leafmap as leafmap
import requests
from PIL import Image

# Basic
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

# Monitoring
from tqdm.notebook import tqdm

# IO
from os.path import join, exists, basename, dirname, splitext, expanduser
from glob import glob
from shapely.geometry import Point
from shapely import vectorized

import geopandas as gpd

# Parallel processing
from joblib import Parallel, delayed
import concurrent.futures as cf

import rioxarray as rxr

# Load environment variables
from dotenv import load_dotenv
load_dotenv()

True

In [197]:
PLANET_API_KEY="PLAKea85382c048b4ba086c40e3823d83d11"
# PLANET_API_KEY = os.getenv("PLANET_API_KEY")
print(PLANET_API_KEY)
assert PLANET_API_KEY is not None
headers = {"Authorization": f"api-key {PLANET_API_KEY}"}
# # params = {
# #     "name__contains": quarter,
# # }

# response = requests.get(f"https://api.planet.com/basemaps/v1/mosaics", headers=headers)
# response.json()

PLAKea85382c048b4ba086c40e3823d83d11


In [198]:
import numpy as np

In [199]:
import os
import leafmap

# Set the Planet API key
PLANET_API_KEY = "PLAKea85382c048b4ba086c40e3823d83d11"
# Alternatively, retrieve the API key from environment variables:
# PLANET_API_KEY = os.getenv()

# Ensure the API key is set
assert PLANET_API_KEY is not None, "PLANET_API_KEY must be set!"
print(PLANET_API_KEY)

# Initialize the map
m = leafmap.Map()

# Add Planet imagery for the first quarter of 2024

m.add_planet_by_quarter(2024, 1, api_key=PLANET_API_KEY)

# Add geometry from the first row of the DataFrame
print(images_with_label.iloc[0:1][['geometry']].reset_index(drop=True))

# Get the geometry from the i-th row of images_with_label
i = np.random.randint(0, len(images_with_label))  
index_right = images_with_label.iloc[i]['index_right']

# Add the corresponding geometry from gdf_labels_webm to the map
m.add_gdf(gdf_labels_webm.iloc[index_right:index_right + 1].reset_index(drop=True), zoom_to_layer=True)

# Display the map
m


PLAKea85382c048b4ba086c40e3823d83d11
                                            geometry
0  POLYGON ((8412355.972 3336932.518, 8415413.454...


Map(center=[20, 0], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title', 'zoom_out_text…

# All states data marge into one file 


In [ ]:
bihar_label_path=f"../data/jcss_processed_data/bihar/labels"
#count the number of labels
label_files = glob(join(bihar_label_path, "*.txt"))
print(f"Number of labels: {len(label_files)}")
haryana_label_path=f"../data/jcss_processed_data/haryana/labels"
#count the number of labels
label_files = glob(join(haryana_label_path, "*.txt"))
print(f"Number of labels: {len(label_files)}")
uttar_pradesh_label_path=f"../data/jcss_processed_data/uttar_pradesh/labels"
#count the number of labels
label_files = glob(join(uttar_pradesh_label_path, "*.txt"))
print(f"Number of labels: {len(label_files)}")
punjab_label_path=f"../data/jcss_processed_data/punjab/labels"
#count the number of labels
label_files = glob(join(punjab_label_path, "*.txt"))
print(f"Number of labels: {len(label_files)}")
west_bengal_label_path=f"../data/jcss_processed_data/west_bengal/labels"
#count the number of labels
label_files = glob(join(west_bengal_label_path, "*.txt"))
print(f"Number of labels: {len(label_files)}")

# all_label_paths=glob("../data/jcss_processed_data/*/labels/*.txt")
# print(f"Total number of labels: {len(all_label_paths)}")


Number of labels: 3771
Number of labels: 1139
Number of labels: 10055
Number of labels: 1589
Number of labels: 1622
Total number of labels: 36352


In [34]:
# make a new directory for the combined data
os.makedirs("../data/jcss_processed_data/combined_data/labels", exist_ok=True)

# copy the labels from each state to the combined data directory using python
for state in ["bihar", "haryana", "uttar_pradesh", "punjab", "west_bengal"]:
    label_files = glob(f"../data/jcss_processed_data/{state}/labels/*.txt")
    for label_file in label_files:
        os.system(f"cp {label_file} ../data/jcss_processed_data/combined_data/labels")



In [242]:
import os
import glob

label_dir = "/home/rishabh.mondal/Brick-Kilns-project/ijcai_2025_kilns/data/combined_data/labels"

# List of patterns for source image directories
patterns = ["/home/rishabh.mondal/Brick-Kilns-project/ijcai_2025_kilns/data/processed_data/*/images", "/home/patel_zeel/kiln_compass_24/data/*/images"]

# Gather all image directories matching the patterns
image_dirs = []
for pattern in patterns:
    image_dirs.extend(glob.glob(pattern))

destination_image_dir = "/home/rishabh.mondal/Brick-Kilns-project/ijcai_2025_kilns/data/combined_data/images"

# Create destination directory if it doesn't exist
os.makedirs(destination_image_dir, exist_ok=True)

# Iterate over all .txt files in the label directory
for label_file in os.listdir(label_dir):
    if label_file.endswith(".txt"):
        # Extract the base filename (without extension)
        base_name = os.path.splitext(label_file)[0]
        # Construct the corresponding .tif filename
        tif_filename = f"{base_name}.tif"

        # Look for the .tif file in any of the source directories
        source_tif_path = None
        for image_dir in image_dirs:
            candidate_path = os.path.join(image_dir, tif_filename)
            if os.path.exists(candidate_path):
                source_tif_path = candidate_path
                break  # Stop searching once the file is found

        # If the file is found, create a symbolic link
        if source_tif_path:
            destination_tif_path = os.path.join(destination_image_dir, tif_filename)
            # Avoid overwriting existing symlinks
            if not os.path.exists(destination_tif_path):
                os.symlink(source_tif_path, destination_tif_path)
                print(f"Linked {source_tif_path} -> {destination_tif_path}")
            else:
                print(f"Symlink already exists for {destination_tif_path}")
        else:
            print(f"File not found: {tif_filename} in any of the source directories.")

print(f"All matching .tif files have been symlinked to {destination_image_dir}")


Linked /home/patel_zeel/kiln_compass_24/data/uttar_pradesh/images/9051063_3086524.tif -> /home/rishabh.mondal/Brick-Kilns-project/ijcai_2025_kilns/data/combined_data/images/9051063_3086524.tif
Linked /home/patel_zeel/kiln_compass_24/data/haryana/images/8556974_3412452.tif -> /home/rishabh.mondal/Brick-Kilns-project/ijcai_2025_kilns/data/combined_data/images/8556974_3412452.tif
Linked /home/patel_zeel/kiln_compass_24/data/uttar_pradesh/images/8885959_3281897.tif -> /home/rishabh.mondal/Brick-Kilns-project/ijcai_2025_kilns/data/combined_data/images/8885959_3281897.tif
Linked /home/patel_zeel/kiln_compass_24/data/bihar/images/9518858_2962391.tif -> /home/rishabh.mondal/Brick-Kilns-project/ijcai_2025_kilns/data/combined_data/images/9518858_2962391.tif
Linked /home/patel_zeel/kiln_compass_24/data/haryana/images/8584492_3544535.tif -> /home/rishabh.mondal/Brick-Kilns-project/ijcai_2025_kilns/data/combined_data/images/8584492_3544535.tif
Linked /home/patel_zeel/kiln_compass_24/data/uttar_prad